In [2]:
import import_ipynb
from arrival_networkx import *
import numpy as np
import random as rm
from typing import List
from collections import deque
import networkx as nx

importing Jupyter notebook from arrival_networkx.ipynb


In [38]:
def multi_run_procedure(instance: Arrival, S_subset: List[int],w : dict):
       
    t = {s:0 for s in instance.vertices}
    
    t[0] = 1     # t[o] ← 1 /* traversal of (Y, o) */
    for v in S_subset:
        t[instance.s_0[v]] += np.ceil(w[v]/2) # /* dwi/2e traversals of (vi, seven(vi)) */
        t[instance.s_1[v]] += np.floor(w[v]/2) # /* bwi/2c traversals of (vi, sodd(vi)) */
    

    # Let scurr and snext be arrays indexed by the vertices of V \ S
    s_curr =  instance.s_0 
    s_next = instance.s_1
            
            
    waiting_set = []
    for v in instance.vertices:
        if v not in S_subset and v not in [instance.target_node, instance.sink_node]:
            waiting_set.append(v)
            
    while len(waiting_set) > 0: ## maintain all the vertices not in S 
        waiting_set_ = [ws for ws in waiting_set if t[ws]>0]
        if not waiting_set_:
            break
        
        choose = rm.choice(waiting_set_)
        tau = rm.randint(1,t[choose])
        
        t[choose] -= tau
        t[s_curr[choose]] += np.ceil(tau/2)
        t[s_next[choose]] += np.floor(tau/2)
        
        if tau & 1 : 
            temp = s_curr[choose]
            s_curr[choose] = s_next[choose]
            s_next[choose] = temp
    # print(t)      
    return t[instance.target_node], t[instance.sink_node], {v:t[v] for v in S_subset}


In [16]:
def decompose_into_layers(graph):
    """
    Decompose the graph into layers based on the distance of the vertices to the destination nodes.
    
    Parameters:
    - graph: A NetworkX graph instance.
    - target_node: The target node (d).
    - sink_node: The sink node (d').
    
    Returns:
    - layers: A dictionary where key is the layer index and value is a list of nodes in that layer.
    - max_dist: The maximum distance (layer index) found.
    """
    
    # Initialize the layers dictionary
    layers = {}
    # Distance dictionary with initial values set to None for each node
    dist = {node: float('inf') for node in graph.nodes()}
    
    # Define a BFS procedure to calculate distances to {target_node, sink_node}
    queue = deque([(instance.target_node, 0), (instance.sink_node, 0)])
    while queue:
        current_node, current_dist = queue.popleft()
        if dist[current_node] == float('inf'):
            dist[current_node] = current_dist
            if current_dist not in layers:
                layers[current_dist] = [current_node]
            else:
                layers[current_dist].append(current_node)
            for neighbor in graph.predecessors(current_node):
                if dist[neighbor] == float('inf'):
                    queue.append((neighbor, current_dist + 1))
    
    # Calculate max_dist
    max_dist = max(dist.values())
    
    return layers, max_dist

In [18]:
def compute_phi_set(instance: Arrival, phi: float) :
    layers, max_dist = decompose_into_layers(instance.graph) 
    # print(layers)
    S = []
    U = layers[0]
    for i in range(1,max_dist+1):
        if len(layers[i]) < phi*len(U):
            S += layers[i]
            U = []
        U += layers[i]
    return S
    

In [35]:
def compare_w(w,w_new):
    # if w is None:
    #     return False
    for key in w:
        if w[key] != w_new[key]:
            return False
    return True

def subexponential(instance: Arrival, phi: float):
    S = compute_phi_set(instance, phi)
    print("S is ",S)
    w = {s:10 for s in S}
    t_d,t_sink, w_new = multi_run_procedure(instance, S, w)
    print(w_new)
    
    while not compare_w(w,w_new):
        w = w_new
        t_d, t_sink, w_new = multi_run_procedure(instance, S, w)
        
    print("t_d is ",t_d, "t_sink is ",t_sink, "w is ",w_new)
        
    return t_d, t_sink, w_new
    
    

# Validating The Algo

In [31]:
def run_procedure(instance: Arrival):
        v = instance.start_node
        s_curr = np.copy(instance.s_0) # current switches for each node
        s_next = np.copy(instance.s_1) # next switch for each node
        counter = 0
        while counter < instance.n * 2**instance.n:
            # if counter % 10**8 == 0:
            print(f'move {counter} :{v}')
            
            if v == -1:
                return False
            elif v == instance.target_node:
                return True
            
            w = s_curr[v]
            s_curr[v] = s_next[v]
            s_next[v] = w  
            v = w
            
            counter += 1
        
        return False

In [69]:
number_of_nodes = 40
phi = np.sqrt(3) / np.sqrt(2*number_of_nodes)
    
for i in range(1):
    # instance = Arrival(number_of_nodes, True)
    instance = get_branch_instance_without_random(number_of_nodes, 0.6)
    out = subexponential(instance, phi) 
    if out[0] > 0 and out[1] == 0:
        if run_procedure(instance):
            print("Success")
        else:
            print("false positive")
        

S is  [33, 18, 27, 12]
{33: 0, 18: 0, 27: 41.0, 12: 0}
t_d is  1.0 t_sink is  0 w is  {33: 3.0, 18: 0, 27: 212.0, 12: 1.0}
move 0 :0
move 1 :1
move 2 :0
move 3 :24
move 4 :0
move 5 :1
move 6 :2
move 7 :0
move 8 :24
move 9 :25
move 10 :0
move 11 :1
move 12 :0
move 13 :24
move 14 :0
move 15 :1
move 16 :2
move 17 :3
move 18 :0
move 19 :24
move 20 :25
move 21 :26
move 22 :0
move 23 :1
move 24 :0
move 25 :24
move 26 :0
move 27 :1
move 28 :2
move 29 :0
move 30 :24
move 31 :25
move 32 :0
move 33 :1
move 34 :0
move 35 :24
move 36 :0
move 37 :1
move 38 :2
move 39 :3
move 40 :4
move 41 :0
move 42 :24
move 43 :25
move 44 :26
move 45 :27
move 46 :0
move 47 :1
move 48 :0
move 49 :24
move 50 :0
move 51 :1
move 52 :2
move 53 :0
move 54 :24
move 55 :25
move 56 :0
move 57 :1
move 58 :0
move 59 :24
move 60 :0
move 61 :1
move 62 :2
move 63 :3
move 64 :0
move 65 :24
move 66 :25
move 67 :26
move 68 :0
move 69 :1
move 70 :0
move 71 :24
move 72 :0
move 73 :1
move 74 :2
move 75 :0
move 76 :24
move 77 :25
move

In [59]:
## Normal random instance
instances = []
def run_random_instance():
    number_of_nodes = 30
    phi = np.sqrt(3) / np.sqrt(2*number_of_nodes)
    # branch_instace = get_branch_instance(number_of_nodes,split_ratio=0.5)
    for i in range(10):
        print("---------------------------------\n","Instance ",i+1)
        instance = Arrival(number_of_nodes, True)
        instances.append(instance)
        
        out = subexponential(instance, phi)
        if out[0] > 0 and out[1] == 0:
            if not run_procedure(instance):
                return instance
    return None
            
instance = run_random_instance()
instance

---------------------------------
 Instance  1
S is  [3, 16, 17]
{3: 4.0, 16: 0, 17: 22.0}
t_d is  1.0 t_sink is  0 w is  {3: 1.0, 16: 0, 17: 6.0}
move 0 :0
move 1 :21
move 2 :5
move 3 :26
move 4 :10
move 5 :7
move 6 :27
move 7 :3
move 8 :17
move 9 :13
move 10 :9
move 11 :13
move 12 :6
move 13 :15
move 14 :6
move 15 :11
move 16 :5
move 17 :11
move 18 :17
move 19 :11
move 20 :5
move 21 :26
move 22 :22
move 23 :9
move 24 :25
move 25 :1
move 26 :10
move 27 :8
move 28 :6
move 29 :15
move 30 :10
move 31 :7
move 32 :14
move 33 :22
move 34 :23
move 35 :28
move 36 :13
move 37 :9
move 38 :13
move 39 :6
move 40 :11
move 41 :17
move 42 :13
move 43 :9
move 44 :25
move 45 :19
move 46 :8
move 47 :29
---------------------------------
 Instance  2
S is  [4, 27, 28, 19]
{4: 5.0, 27: 0, 28: 9.0, 19: 3.0}
t_d is  1.0 t_sink is  0 w is  {4: 0.0, 27: 0, 28: 0.0, 19: 0}
move 0 :0
move 1 :15
move 2 :6
move 3 :2
move 4 :24
move 5 :28
move 6 :15
move 7 :0
move 8 :3
move 9 :5
move 10 :15
move 11 :6
move 12 :0
m

In [ ]:
## BRANCH Instances 
number_of_nodes = 30
weird_instances = []
non_terminal_instances = []
instances = []
phi = np.sqrt(3) / np.sqrt(2*number_of_nodes)
for i in range(20):    
    r = np.random.uniform(0.1, 0.9)
    instance = get_branch_instance(number_of_nodes, split_ratio=r)
    instances.append(instance)
    
    out = subexponential(instance, phi)
    if out[0] == 0 and out[1] == 0:
        weird_instances.append(i)
    elif out[0] == 0 and out[1] != 0:
        non_terminal_instances.append(i)

In [67]:
### Branch without random 
number_of_nodes = 30
weird_instances = []
non_terminal_instances = []
instances = []
phi = np.sqrt(3) / np.sqrt(2*number_of_nodes)
for i in range(1):
        print("---------------------------------\n","Instance ",i+1)
        instance = get_branch_instance_without_random(number_of_nodes, split_ratio=0.4)
        instances.append(instance)
        
        out = subexponential(instance, phi)
        if out[0] > 0:
            if not run_procedure(instance):
                break

---------------------------------
 Instance  1
S is  [24, 7, 19, 2]
{24: 0, 7: 0, 19: 0.0, 2: 41.0}
t_d is  0 t_sink is  1.0 w is  {24: 0, 7: 3.0, 19: 2.0, 2: 102.0}
